In [295]:
import pandas as pd
import optuna as opt
import wandb
from catboost import CatBoostClassifier
from sklearn.model_selection import cross_val_score
from sklearn.impute import KNNImputer

def objective(trial):
    params = {
        'iterations': trial.suggest_int('iterations', 100, 750),
        'learning_rate': trial.suggest_loguniform('learning_rate', 0.001, 0.1),
        'depth': trial.suggest_int('depth', 2, 10),
    }

    model = CatBoostClassifier(**params, random_state=42)

    score = cross_val_score(model, X, y, cv=3, scoring='accuracy').mean()
    
    wandb.log({"iterations": params['iterations'],
               "learning_rate": params['learning_rate'],
               "depth": params['depth'],
               "accuracy": score})

    return score

wandb.init(project='test')

df = pd.read_csv('../train.csv')
df = df.drop(columns=['Name', 'PassengerId'])

binary_features = ['VIP', 'CryoSleep']
cryo_sleep_depending_features = ['RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck']
categorical_features_without_cabin = ['HomePlanet', 'Destination']
categorical_features_cleared = ['HomePlanet', 'Destination', 'Deck', 'Side']
numerical_features = ['ShoppingMall', 'Spa', 'VRDeck', 'RoomService', 'FoodCourt', 'Age']
imputer = KNNImputer(n_neighbors=1)

for i in range(len(df)):
    if df.at[i, 'CryoSleep'] == True:
        for feature in cryo_sleep_depending_features:
            df.at[i, feature] = 0.0

rows_with_many_missing_values = df[df.isna().sum(axis=1) > 1]
rows_with_one_missing_value = df[df.isna().sum(axis=1) == 1]
df = df.dropna()     
df[["Deck", "CabinNumber", "Side"]] = df["Cabin"].str.split("/", expand=True)
df = df.drop(columns=['Cabin', 'CabinNumber'])
df = df.astype({'CryoSleep': int, 'VIP': int, 'Transported': int})
df = pd.get_dummies(df, columns=categorical_features_cleared)

for feature in numerical_features:
    rows_with_missing_feature = rows_with_one_missing_value[rows_with_one_missing_value[feature].isna()] 
    rows_with_missing_feature[["Deck", "CabinNumber", "Side"]] = rows_with_missing_feature["Cabin"].str.split("/", expand=True)
    rows_with_missing_feature = rows_with_missing_feature.drop(columns=['Cabin', 'CabinNumber'])
    rows_with_missing_feature = rows_with_missing_feature.astype({'CryoSleep': int, 'VIP': int, 'Transported': int})
    rows_with_missing_feature = pd.get_dummies(rows_with_missing_feature, columns=categorical_features_cleared)
    df = pd.concat([df, rows_with_missing_feature], ignore_index=True)
    df = pd.DataFrame(imputer.fit_transform(df), columns=df.columns)

for feature in categorical_features_without_cabin:
    rows_with_missing_feature = rows_with_one_missing_value[rows_with_one_missing_value[feature].isna()] 
    rows_with_missing_feature[["Deck", "CabinNumber", "Side"]] = rows_with_missing_feature["Cabin"].str.split("/", expand=True)
    rows_with_missing_feature = rows_with_missing_feature.drop(columns=['Cabin', 'CabinNumber'])
    rows_with_missing_feature = rows_with_missing_feature.astype({'CryoSleep': int, 'VIP': int, 'Transported': int})
    rows_with_missing_feature = pd.get_dummies(rows_with_missing_feature, columns=categorical_features_cleared)
    df = pd.concat([df, rows_with_missing_feature], ignore_index=True)
    df = pd.DataFrame(imputer.fit_transform(df), columns=df.columns)

for feature in binary_features:
    rows_with_missing_feature = rows_with_one_missing_value[rows_with_one_missing_value[feature].isna()] 
    rows_with_missing_feature[["Deck", "CabinNumber", "Side"]] = rows_with_missing_feature["Cabin"].str.split("/", expand=True)
    rows_with_missing_feature = rows_with_missing_feature.drop(columns=['Cabin', 'CabinNumber'])
    rows_with_missing_feature = pd.get_dummies(rows_with_missing_feature, columns=categorical_features_cleared)
    df = pd.concat([df, rows_with_missing_feature], ignore_index=True)
    df = pd.DataFrame(imputer.fit_transform(df), columns=df.columns)

rows_with_missing_feature = rows_with_one_missing_value[rows_with_one_missing_value['Cabin'].isna()] 
rows_with_missing_feature = rows_with_missing_feature.drop(columns='Cabin')
rows_with_missing_feature = rows_with_missing_feature.astype({'CryoSleep': int, 'VIP': int, 'Transported': int})
rows_with_missing_feature = pd.get_dummies(rows_with_missing_feature, columns=categorical_features_without_cabin)
df = pd.concat([df, rows_with_missing_feature], ignore_index=True)
df = pd.DataFrame(imputer.fit_transform(df), columns=df.columns)

rows_with_many_missing_values = rows_with_many_missing_values.drop(columns='Cabin')

df = pd.concat([df, rows_with_missing_feature], ignore_index=True)
df = pd.DataFrame(imputer.fit_transform(df), columns=df.columns)

target = 'Transported'
X = df.drop(columns=target)
y = df[target]

study = opt.create_study(direction='maximize')
study.optimize(objective, n_trials=50)

best_params = study.best_params
wandb.config.update(best_params)
print("Лучшие параметры:", best_params)

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:wandb: ERROR API key must be 40 characters long, yours was 1
wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
w

C:\Users\vitya\AppData\Local\Temp\ipykernel_5568\3384526075.py:53: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rows_with_missing_feature[["Deck", "CabinNumber", "Side"]] = rows_with_missing_feature["Cabin"].str.split("/", expand=True)
C:\Users\vitya\AppData\Local\Temp\ipykernel_5568\3384526075.py:53: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rows_with_missing_feature[["Deck", "CabinNumber", "Side"]] = rows_with_missing_feature["Cabin"].str.split("/", expand=True)
C:\Users\vitya\AppData\Local\Temp\ipyk

0:	learn: 0.6837783	total: 4.05ms	remaining: 595ms
1:	learn: 0.6739856	total: 7.8ms	remaining: 570ms
2:	learn: 0.6645259	total: 11.3ms	remaining: 548ms
3:	learn: 0.6569174	total: 14.7ms	remaining: 528ms
4:	learn: 0.6476460	total: 17.9ms	remaining: 513ms
5:	learn: 0.6386661	total: 21.4ms	remaining: 507ms
6:	learn: 0.6306759	total: 25.1ms	remaining: 505ms
7:	learn: 0.6233864	total: 28.6ms	remaining: 500ms
8:	learn: 0.6157611	total: 32.2ms	remaining: 497ms
9:	learn: 0.6097107	total: 35.5ms	remaining: 489ms
10:	learn: 0.6032884	total: 38.8ms	remaining: 483ms
11:	learn: 0.5967160	total: 42.1ms	remaining: 477ms
12:	learn: 0.5908988	total: 45.4ms	remaining: 472ms
13:	learn: 0.5848674	total: 48.7ms	remaining: 466ms
14:	learn: 0.5801237	total: 52.2ms	remaining: 463ms
15:	learn: 0.5742663	total: 55.6ms	remaining: 459ms
16:	learn: 0.5690673	total: 58.8ms	remaining: 453ms
17:	learn: 0.5644588	total: 62.2ms	remaining: 449ms
18:	learn: 0.5605516	total: 65.7ms	remaining: 446ms
19:	learn: 0.5544412	to

[I 2024-02-19 11:41:10,830] Trial 0 finished with value: 0.7978686833963562 and parameters: {'iterations': 148, 'learning_rate': 0.016437566675090897, 'depth': 8}. Best is trial 0 with value: 0.7978686833963562.
C:\Users\vitya\AppData\Local\Temp\ipykernel_5568\3384526075.py:11: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.001, 0.1),


0:	learn: 0.6889918	total: 1.25ms	remaining: 442ms
1:	learn: 0.6857591	total: 2.39ms	remaining: 423ms
2:	learn: 0.6826931	total: 3.51ms	remaining: 412ms
3:	learn: 0.6788005	total: 4.68ms	remaining: 411ms
4:	learn: 0.6758931	total: 5.8ms	remaining: 406ms
5:	learn: 0.6728619	total: 6.9ms	remaining: 402ms
6:	learn: 0.6699920	total: 7.97ms	remaining: 396ms
7:	learn: 0.6670526	total: 9.12ms	remaining: 395ms
8:	learn: 0.6641604	total: 10.2ms	remaining: 394ms
9:	learn: 0.6613835	total: 11.6ms	remaining: 399ms
10:	learn: 0.6587872	total: 12.8ms	remaining: 399ms
11:	learn: 0.6561966	total: 14.1ms	remaining: 403ms
12:	learn: 0.6535425	total: 15.3ms	remaining: 403ms
13:	learn: 0.6503891	total: 16.6ms	remaining: 404ms
14:	learn: 0.6478968	total: 17.8ms	remaining: 405ms
15:	learn: 0.6456222	total: 19.1ms	remaining: 404ms
16:	learn: 0.6433296	total: 20.3ms	remaining: 403ms
17:	learn: 0.6409550	total: 21.6ms	remaining: 405ms
18:	learn: 0.6387182	total: 22.9ms	remaining: 406ms
19:	learn: 0.6358182	tot

...

538:	learn: 0.3904830	total: 695ms	remaining: 63.1ms
539:	learn: 0.3904271	total: 696ms	remaining: 61.9ms
540:	learn: 0.3903693	total: 697ms	remaining: 60.6ms
541:	learn: 0.3903270	total: 699ms	remaining: 59.3ms
542:	learn: 0.3902532	total: 700ms	remaining: 58ms
543:	learn: 0.3902229	total: 701ms	remaining: 56.7ms
544:	learn: 0.3901834	total: 703ms	remaining: 55.4ms
545:	learn: 0.3901022	total: 704ms	remaining: 54.2ms
546:	learn: 0.3900426	total: 705ms	remaining: 52.9ms
547:	learn: 0.3900227	total: 707ms	remaining: 51.6ms
548:	learn: 0.3899808	total: 708ms	remaining: 50.3ms
549:	learn: 0.3899738	total: 710ms	remaining: 49ms
550:	learn: 0.3899190	total: 711ms	remaining: 47.8ms
551:	learn: 0.3898812	total: 713ms	remaining: 46.5ms
552:	learn: 0.3897701	total: 714ms	remaining: 45.2ms
553:	learn: 0.3897399	total: 716ms	remaining: 43.9ms
554:	learn: 0.3896795	total: 718ms	remaining: 42.7ms
555:	learn: 0.3896492	total: 719ms	remaining: 41.4ms
556:	learn: 0.3896336	total: 721ms	remaining: 40.1

C:\Users\vitya\AppData\Local\Temp\ipykernel_5568\3384526075.py:11: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.001, 0.1),


42:	learn: 0.4639382	total: 82.8ms	remaining: 605ms
43:	learn: 0.4623457	total: 84.7ms	remaining: 602ms
44:	learn: 0.4605869	total: 86.5ms	remaining: 600ms
45:	learn: 0.4593007	total: 88.3ms	remaining: 597ms
46:	learn: 0.4576794	total: 90.2ms	remaining: 595ms
47:	learn: 0.4560993	total: 92ms	remaining: 592ms
48:	learn: 0.4549986	total: 93.9ms	remaining: 590ms
49:	learn: 0.4538210	total: 95.7ms	remaining: 587ms
50:	learn: 0.4525297	total: 97.9ms	remaining: 587ms
51:	learn: 0.4517936	total: 99.9ms	remaining: 586ms
52:	learn: 0.4505508	total: 102ms	remaining: 583ms
53:	learn: 0.4494075	total: 104ms	remaining: 581ms
54:	learn: 0.4481479	total: 105ms	remaining: 579ms
55:	learn: 0.4471380	total: 107ms	remaining: 576ms
56:	learn: 0.4464484	total: 109ms	remaining: 574ms
57:	learn: 0.4453126	total: 111ms	remaining: 571ms
58:	learn: 0.4443601	total: 113ms	remaining: 570ms
59:	learn: 0.4430400	total: 115ms	remaining: 568ms
60:	learn: 0.4418511	total: 117ms	remaining: 566ms
61:	learn: 0.4409718	to

[I 2024-02-19 11:45:20,532] Trial 49 finished with value: 0.8037126160192507 and parameters: {'iterations': 357, 'learning_rate': 0.03020067155054127, 'depth': 5}. Best is trial 13 with value: 0.8079523318437034.


334:	learn: 0.3694248	total: 630ms	remaining: 41.4ms
335:	learn: 0.3692098	total: 632ms	remaining: 39.5ms
336:	learn: 0.3690991	total: 634ms	remaining: 37.6ms
337:	learn: 0.3689822	total: 636ms	remaining: 35.7ms
338:	learn: 0.3688486	total: 638ms	remaining: 33.9ms
339:	learn: 0.3686244	total: 639ms	remaining: 32ms
340:	learn: 0.3684090	total: 641ms	remaining: 30.1ms
341:	learn: 0.3683032	total: 643ms	remaining: 28.2ms
342:	learn: 0.3681583	total: 645ms	remaining: 26.3ms
343:	learn: 0.3679999	total: 647ms	remaining: 24.4ms
344:	learn: 0.3678756	total: 649ms	remaining: 22.6ms
345:	learn: 0.3676902	total: 650ms	remaining: 20.7ms
346:	learn: 0.3675974	total: 652ms	remaining: 18.8ms
347:	learn: 0.3673594	total: 654ms	remaining: 16.9ms
348:	learn: 0.3671894	total: 656ms	remaining: 15ms
349:	learn: 0.3670329	total: 658ms	remaining: 13.2ms
350:	learn: 0.3669033	total: 660ms	remaining: 11.3ms
351:	learn: 0.3666223	total: 662ms	remaining: 9.4ms
352:	learn: 0.3665281	total: 664ms	remaining: 7.52m